In [91]:
import torch
roberta = torch.hub.load('pytorch/fairseq', 'roberta.large')
roberta.eval()  # disable dropout (or leave in train mode to finetune)

Using cache found in /Users/chrishuber/.cache/torch/hub/pytorch_fairseq_main
2022-03-21 15:33:12 | INFO | fairseq.file_utils | loading archive file http://dl.fbaipublicfiles.com/fairseq/models/roberta.large.tar.gz from cache at /Users/chrishuber/.cache/torch/pytorch_fairseq/83e3a689e28e5e4696ecb0bbb05a77355444a5c8a3437e0f736d8a564e80035e.c687083d14776c1979f3f71654febb42f2bb3d9a94ff7ebdfe1ac6748dba89d2
/opt/anaconda3/lib/python3.9/site-packages/hydra/experimental/initialize.py:35: UserWarning: hydra.experimental.initialize() is no longer experimental. Use hydra.initialize()
  deprecation_warning(
/opt/anaconda3/lib/python3.9/site-packages/hydra/experimental/compose.py:18: UserWarning: hydra.experimental.compose() is no longer experimental. Use hydra.compose()
  deprecation_warning(
/opt/anaconda3/lib/python3.9/site-packages/hydra/core/default_element.py:122: UserWarning: In 'config': Usage of deprecated keyword in package header '# @package _group_'.
See https://hydra.cc/docs/next/upgra

RobertaHubInterface(
  (model): RobertaModel(
    (encoder): RobertaEncoder(
      (sentence_encoder): TransformerEncoder(
        (dropout_module): FairseqDropout()
        (embed_tokens): Embedding(50265, 1024, padding_idx=1)
        (embed_positions): LearnedPositionalEmbedding(514, 1024, padding_idx=1)
        (layernorm_embedding): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
        (layers): ModuleList(
          (0): TransformerEncoderLayerBase(
            (self_attn): MultiheadAttention(
              (dropout_module): FairseqDropout()
              (k_proj): Linear(in_features=1024, out_features=1024, bias=True)
              (v_proj): Linear(in_features=1024, out_features=1024, bias=True)
              (q_proj): Linear(in_features=1024, out_features=1024, bias=True)
              (out_proj): Linear(in_features=1024, out_features=1024, bias=True)
            )
            (self_attn_layer_norm): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
            (dr

In [92]:
tokens = roberta.encode('Hello world!')
assert tokens.tolist() == [0, 31414, 232, 328, 2]
assert roberta.decode(tokens) == 'Hello world!'

In [93]:
# Extract the last layer's features
last_layer_features = roberta.extract_features(tokens)
assert last_layer_features.size() == torch.Size([1, 5, 1024])

# Extract all layer's features (layer 0 is the embedding layer)
all_layers = roberta.extract_features(tokens, return_all_hiddens=True)
assert len(all_layers) == 25
assert torch.all(all_layers[-1] == last_layer_features)

In [94]:
# Download RoBERTa already finetuned for MNLI
roberta = torch.hub.load('pytorch/fairseq', 'roberta.large.mnli')
roberta.eval()  # disable dropout for evaluation

with torch.no_grad():
    # Encode a pair of sentences and make a prediction
    tokens = roberta.encode('Roberta is a heavily optimized version of BERT.', 'Roberta is not very optimized.')
    prediction = roberta.predict('mnli', tokens).argmax().item()
    assert prediction == 0  # contradiction

    # Encode another pair of sentences
    tokens = roberta.encode('Roberta is a heavily optimized version of BERT.', 'Roberta is based on BERT.')
    prediction = roberta.predict('mnli', tokens).argmax().item()
    assert prediction == 2  # entailment

Using cache found in /Users/chrishuber/.cache/torch/hub/pytorch_fairseq_main
2022-03-21 15:33:58 | INFO | fairseq.file_utils | loading archive file http://dl.fbaipublicfiles.com/fairseq/models/roberta.large.mnli.tar.gz from cache at /Users/chrishuber/.cache/torch/pytorch_fairseq/7685ba8546f9a5ce1a00c7a6d7d44f7e748d22681172f0f391c3d48f487c801c.74e37d47306b3cc51c5f8d335022a392c29f1906c8cd9e9cd3446d7422cf55d8
2022-03-21 15:33:59 | INFO | fairseq.tasks.masked_lm | dictionary: 50264 types
2022-03-21 15:34:12 | INFO | fairseq.models.roberta.model | {'_name': None, 'common': {'_name': None, 'no_progress_bar': False, 'log_interval': 100, 'log_format': 'json', 'log_file': None, 'tensorboard_logdir': None, 'wandb_project': None, 'azureml_logging': False, 'seed': 8, 'cpu': False, 'tpu': False, 'bf16': False, 'memory_efficient_bf16': False, 'fp16': True, 'memory_efficient_fp16': False, 'fp16_no_flatten_grads': False, 'fp16_init_scale': 4, 'fp16_scale_window': 128, 'fp16_scale_tolerance': 0.0, 'on_

In [95]:
roberta.register_classification_head('new_task', num_classes=3)
logprobs = roberta.predict('new_task', tokens)  # tensor([[-1.1050, -1.0672, -1.1245]], grad_fn=<LogSoftmaxBackward>)

In [96]:
print(logprobs)
print(logprobs.argmax(dim=1))

tensor([[-0.9322, -1.0115, -1.4162]], grad_fn=<LogSoftmaxBackward0>)
tensor([0])


In [97]:
# Encode a pair of sentences and make a prediction
tokens = roberta.encode('Roberta is a heavily optimized version of BERT.', 'Roberta is not very optimized.')
roberta.predict('mnli', tokens).argmax()  # 0: contradiction

tensor(0)

In [98]:
# Encode another pair of sentences
tokens = roberta.encode('Roberta is a heavily optimized version of BERT.', 'Roberta is based on BERT.')
roberta.predict('mnli', tokens).argmax()  # 2: entailment

tensor(2)

In [99]:
# Trying sentences of my own
tokens = roberta.encode('China is a country in Asia.', 'China is an Asian country.')
roberta.predict('mnli', tokens).argmax()  # 2: entailment

tensor(2)

In [100]:
# Trying sentences of my own
tokens = roberta.encode('I am a boy.', 'I am not a boy.')
roberta.predict('mnli', tokens).argmax()  # 2: entailment

tensor(0)

In [85]:
from fairseq.data.data_utils import collate_tokens

batch_of_pairs = [
    ['Roberta is a heavily optimized version of BERT.', 'Roberta is not very optimized.'],
    ['Roberta is a heavily optimized version of BERT.', 'Roberta is based on BERT.'],
    ['potatoes are awesome.', 'I like to run.'],
    ['Mars is very far from earth.', 'Mars is very close.'],
]

batch = collate_tokens(
    [roberta.encode(pair[0], pair[1]) for pair in batch_of_pairs], pad_idx=1
)

logprobs = roberta.predict('mnli', batch)
print(logprobs.argmax(dim=1))

tensor([0, 2, 1, 0])


In [ ]:
### START HERE

In [2]:
import torch

# Download RoBERTa already finetuned for MNLI
roberta = torch.hub.load('pytorch/fairseq', 'roberta.large.mnli')
roberta.eval()  # disable dropout for evaluation

Using cache found in /Users/chrishuber/.cache/torch/hub/pytorch_fairseq_main
2022-03-21 10:35:23 | INFO | fairseq.tasks.text_to_speech | Please install tensorboardX: pip install tensorboardX
2022-03-21 10:35:23 | INFO | fairseq.file_utils | loading archive file http://dl.fbaipublicfiles.com/fairseq/models/roberta.large.mnli.tar.gz from cache at /Users/chrishuber/.cache/torch/pytorch_fairseq/7685ba8546f9a5ce1a00c7a6d7d44f7e748d22681172f0f391c3d48f487c801c.74e37d47306b3cc51c5f8d335022a392c29f1906c8cd9e9cd3446d7422cf55d8
/opt/anaconda3/lib/python3.9/site-packages/hydra/experimental/initialize.py:35: UserWarning: hydra.experimental.initialize() is no longer experimental. Use hydra.initialize()
  deprecation_warning(
/opt/anaconda3/lib/python3.9/site-packages/hydra/experimental/compose.py:18: UserWarning: hydra.experimental.compose() is no longer experimental. Use hydra.compose()
  deprecation_warning(
/opt/anaconda3/lib/python3.9/site-packages/hydra/core/default_element.py:122: UserWarning

RobertaHubInterface(
  (model): RobertaModel(
    (encoder): RobertaEncoder(
      (sentence_encoder): TransformerEncoder(
        (dropout_module): FairseqDropout()
        (embed_tokens): Embedding(50265, 1024, padding_idx=1)
        (embed_positions): LearnedPositionalEmbedding(514, 1024, padding_idx=1)
        (layernorm_embedding): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
        (layers): ModuleList(
          (0): TransformerEncoderLayerBase(
            (self_attn): MultiheadAttention(
              (dropout_module): FairseqDropout()
              (k_proj): Linear(in_features=1024, out_features=1024, bias=True)
              (v_proj): Linear(in_features=1024, out_features=1024, bias=True)
              (q_proj): Linear(in_features=1024, out_features=1024, bias=True)
              (out_proj): Linear(in_features=1024, out_features=1024, bias=True)
            )
            (self_attn_layer_norm): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
            (dr

In [86]:
train_df = pd.read_json("./multinli_1.0/multinli_1.0_dev_matched.jsonl", lines=True)
train_df.head(5)

annotator_labels       genre  \
0   [neutral, entailment, neutral, neutral, neutral]       slate   
1  [contradiction, contradiction, contradiction, ...  government   
2  [entailment, entailment, entailment, entailmen...   telephone   
3  [contradiction, contradiction, contradiction, ...   telephone   
4  [contradiction, contradiction, contradiction, ...   telephone   

      gold_label  pairID  promptID  \
0        neutral  63735n     63735   
1  contradiction  91383c     91383   
2     entailment    755e       755   
3  contradiction  78013c     78013   
4  contradiction  96377c     96377   

                                           sentence1  \
0                     The new rights are nice enough   
1  This site includes a list of all award winners...   
2  uh i don't know i i have mixed emotions about ...   
3  yeah i i think my favorite restaurant is alway...   
4         i don't know um do you do a lot of camping   

                              sentence1_binary_parse  \
0  ( ( The ( new rights ) ) ( are ( nice enough )...   
1  ( ( This site ) ( ( includes ( ( ( ( a list ) ...   
2  ( ( ( ( uh ( i ( ( do n't ) ( know ( ( i i ) (...   
3  ( yeah ( ( i i ) ( think ( ( my ( favorite res...   
4  ( i ( ( do n't ) ( know ( um ( do ( you ( do (...   

                                     sentence1_parse  \
0  (ROOT (S (NP (DT The) (JJ new) (NNS rights)) (...   
1  (ROOT (S (NP (DT This) (NN site)) (VP (VBZ inc...   
2  (ROOT (SINV (S (S (INTJ (UH uh)) (NP (FW i)) (...   
3  (ROOT (S (VP (VB yeah) (NP (NP (FW i) (FW i)) ...   
4  (ROOT (S (NP (FW i)) (VP (VBP do) (RB n't) (VP...   

                                           sentence2  \
0         Everyone really likes the newest benefits    
1  The Government Executive articles housed on th...   
2  I like him for the most part, but would still ...   
3  My favorite restaurants are always at least a ...   
4                                    I know exactly.   

                              sentence2_binary_parse  \
0  ( Everyone ( really ( likes ( the ( newest ben...   
1  ( ( ( The ( Government ( Executive articles ) ...   
2  ( I ( ( ( ( ( ( like him ) ( for ( the ( most ...   
3  ( ( My ( favorite restaurants ) ) ( ( ( ( are ...   
4                       ( I ( ( know exactly ) . ) )   

                                     sentence2_parse  
0  (ROOT (S (NP (NN Everyone)) (VP (ADVP (RB real...  
1  (ROOT (S (NP (NP (DT The) (NNP Government) (NN...  
2  (ROOT (S (NP (PRP I)) (VP (VP (VBP like) (NP (...  
3  (ROOT (S (NP (PRP$ My) (JJ favorite) (NNS rest...  
4  (ROOT (S (NP (PRP I)) (VP (VBP know) (ADVP (RB...

In [87]:
print(train_df.shape[0])

10000


In [53]:
train_labels = train_df['annotator_labels']
train_s1 = train_df['sentence1']
train_s2 = train_df['sentence2']
print(train_s1[0])
print(train_s2[0])
print(train_labels[0])

The new rights are nice enough
Everyone really likes the newest benefits 
['neutral', 'entailment', 'neutral', 'neutral', 'neutral']


In [90]:
%%time
# This uses the pretrained Roberta MLNI model to make predictions about what class the two sentences are and assigns the output to a list
preds = []
with torch.no_grad():
    for k in range(len(train_labels)):
        # Encode a pair of sentences and make a prediction
        print("Pair " + str(k) + ":")
        print(train_s1[k], train_s2[k])
        tokens = roberta.encode(train_s1[k], train_s2[k])
        prediction = roberta.predict('mnli', tokens).argmax().item()
        preds.append(prediction)
        print(prediction, train_labels[k])
        print("-----------------")
        # assert prediction == train_labels[0][1]  # contradiction
print("done!")

The new rights are nice enough Everyone really likes the newest benefits 
1 ['neutral', 'entailment', 'neutral', 'neutral', 'neutral']
-----------------
This site includes a list of all award winners and a searchable database of Government Executive articles. The Government Executive articles housed on the website are not able to be searched.
0 ['contradiction', 'contradiction', 'contradiction', 'contradiction', 'contradiction']
-----------------
uh i don't know i i have mixed emotions about him uh sometimes i like him but at the same times i love to see somebody beat him I like him for the most part, but would still enjoy seeing someone beat him.
2 ['entailment', 'entailment', 'entailment', 'entailment', 'entailment']
-----------------
yeah i i think my favorite restaurant is always been the one closest  you know the closest as long as it's it meets the minimum criteria you know of good food My favorite restaurants are always at least a hundred miles away from my house. 
0 ['contradic

2 ['entailment', 'entailment', 'contradiction', 'entailment', 'entailment']
-----------------
Mortifyingly enough, it is all  the difficulty, the laziness, the pathetic formlessness in youth, the round peg in the square hole, the whatever do you want? Many youth are lazy.
2 ['entailment', 'neutral', 'entailment', 'neutral', 'entailment']
-----------------
Conversely, an increase in government saving adds to the supply of resources available for investment and may put downward pressure on interest rates. Interest rates should increase to increase saving.
0 ['neutral', 'contradiction', 'contradiction', 'contradiction', 'contradiction']
-----------------
Britain's best-selling tabloid, the Sun , announced as a front-page world exclusive Friday that Texan model Jerry Hall has started divorce proceedings against aging rock star Mick Jagger at the High Court in London. There is a British publication called the Sun.
2 ['entailment', 'entailment', 'entailment', 'entailment', 'entailment']
----

1 ['neutral', 'neutral', 'contradiction', 'neutral', 'neutral']
-----------------
He had never felt better. The medicine he had taken had worked well.
1 ['neutral', 'neutral', 'neutral', 'neutral', 'neutral']
-----------------
The campaigns seem to reach a new pool of contributors. New people chose to donate to the cause 
2 ['neutral', 'entailment', 'entailment', 'entailment', 'entailment']
-----------------
The Data Warehousing Institute provides education and training in the data warehousing and business intelligence industry. Business intelligence industry is a new and promising field of study.
1 ['neutral', 'neutral', 'neutral', 'neutral', 'neutral']
-----------------
the net cost of operations. The gross cost.
0 ['contradiction', 'contradiction', 'contradiction', 'contradiction', 'contradiction']
-----------------
Credibility is a vital factor, and Jim Lehrer does, indeed, have it. Jim Lehrer has no credibility whatsoever.
0 ['contradiction', 'contradiction', 'contradiction', 'con

2 ['entailment', 'entailment', 'entailment', 'entailment', 'entailment']
-----------------
Visit at sundown or out of season to get the full flavor of the setting. The setting is better to visit at sundown or during low season.
2 ['entailment', 'entailment', 'entailment', 'entailment', 'entailment']
-----------------
In a further role reversal, Gingrich may have positioned himself to fill it. Gingrich should not be in power.
1 ['neutral', 'neutral', 'neutral', 'neutral', 'neutral']
-----------------
All of the islands are now officially and proudly part of France, not colonies as they were for some three centuries. The islands are part of France now instead of just colonies.
2 ['entailment', 'entailment', 'entailment', 'entailment', 'entailment']
-----------------
(For more information on BLM's senior executive performance plans, see app. BLM's performance plans are visible online.
2 ['neutral', 'entailment', 'entailment', 'neutral', 'entailment']
-----------------
While parents may pi

2 ['entailment', 'entailment', 'entailment', 'entailment', 'entailment']
-----------------
Strategic parents might spend a large portion of their tax cuts, causing interest rates to rise. Tax cuts geared to parents will give them greater spending flexibility but will also lead to higher interest rates on loans.
1 ['neutral', 'neutral', 'neutral', 'entailment', 'neutral']
-----------------
However, in the off-field (sentimental) tournament, the Falcons and Jets have more appealing story lines. The Jets and Falcons have boring stories.
0 ['contradiction', 'contradiction', 'contradiction', 'contradiction', 'contradiction']
-----------------
right after the war Just after the war ended.
2 ['entailment', 'entailment', 'entailment', 'entailment', 'entailment']
-----------------
i'm kind of familiar with the weather out that way in west Texas but not in not in Lewisville I do not know the weather conditions in Lewisville.  
2 ['entailment', 'entailment', 'entailment', 'entailment', 'entailmen

...

1 ['neutral', 'neutral', 'neutral', 'neutral', 'neutral']
-----------------
But there are two kinds of  the pleasure of doing, and the pleasure of not doing; the pleasure of indulging, and the pleasure of abstinence. But there are two kinds of the pleasure of doing, and the pleasure of not doing.
2 ['entailment', 'entailment', 'entailment', 'entailment', 'entailment']
-----------------
Miller claimed the First Amendment (right to freedom of speech and association) rather than taking the Fifth (right against self-incrimination). The man did not plead the Fifth.
2 ['entailment', 'entailment', 'entailment', 'entailment', 'contradiction']
-----------------
i don't know she said they go crazy She stated that they remained calm and sane.
0 ['contradiction', 'contradiction', 'contradiction', 'contradiction', 'contradiction']
-----------------
yes i i always turn on the TV set and it seems like i catch that program in the last five minutes and I wish I was able to see more of that program.
1 [

2 ['neutral', 'neutral', 'entailment', 'neutral', 'neutral']
-----------------
an d now we got the governor she's going to do that Now we have the governor and she is going to do that.
2 ['entailment', 'entailment', 'entailment', 'entailment', 'entailment']
-----------------
The chart to which Reich refers was actually presented during Saxton's opening statement, hours before Reich testified, and did not look as Reich claims it did. Reich refers to a chart that he understood well.
1 ['contradiction', 'neutral', 'neutral', 'neutral', 'neutral']
-----------------
He watched San'doro silent in his thoughts. The man made lots of noise.
0 ['contradiction', 'contradiction', 'contradiction', 'contradiction', 'contradiction']
-----------------
Hence, it appears likely that the proportion of LC to AO mail is less for inbound mail than for outbound. It looks like the proportion of LC to AO mail is less for inbound mail than for outbound, said the manager.
1 ['neutral', 'neutral', 'neutral', 'neu

0 ['contradiction', 'contradiction', 'contradiction', 'contradiction', 'neutral']
-----------------
These runs could cost far more than the value of the small improvement in service. The runs are small compared to the improvement in service.
2 ['contradiction', 'contradiction', 'contradiction', 'contradiction', 'contradiction']
-----------------
The 28 sta?­tues representing the kings of Judah and Israel have been remodeled after the drawings of Viollet-le-Duc; the original ones were pulled down during the Revolution, since they were thought to be the kings of France. The people who pulled down the statues were executed.
1 ['neutral', 'neutral', 'neutral', 'neutral', 'neutral']
-----------------
In Loco Parentis Returnus Located in Loco Parentis.
2 ['entailment', 'neutral', 'contradiction', 'neutral', 'neutral']
-----------------
The advent of the Bronze Age (about 3200 b.c. ), and the spread of city-states ruled by kings, is marked by the appearance of royal tombs containing bronze ob

0 ['contradiction', 'contradiction', 'contradiction', 'contradiction', 'contradiction']
-----------------
yeah yeah yeah well because that's the way they they might seem outwardly but boy there's a lots going on in there What you see on the surface is all of it.
0 ['contradiction', 'contradiction', 'contradiction', 'contradiction', 'contradiction']
-----------------
More to the point, even as the major airlines have been reaping large profits over the last four years, their productivity has not risen at all, suggesting that consolidation is not improving efficiency. Though large airlines are making a big profit, they arent any more productive. 
2 ['entailment', 'entailment', 'entailment', 'entailment', 'entailment']
-----------------
Simmons, probably rap's greatest entrepreneur, lives in New York; schmoozes bankers, fashion designers, and record executives; and cuts deals with conglomerates such as Time Warner. Simmons lives in New York and schmoozes fashion designers. 


KeyboardInterrupt: 

In [ ]:
print(len(preds))

In [102]:
test_df = pd.read_json("./input/multinli_0.9_test_matched_unlabeled.jsonl", lines=True)
test_df.head(5)

annotator_labels       genre gold_label  pairID  \
0  [hidden, hidden, hidden, hidden, hidden]       slate     hidden    9847   
1  [hidden, hidden, hidden, hidden, hidden]  government     hidden    9848   
2  [hidden, hidden, hidden, hidden, hidden]     fiction     hidden    9849   
3  [hidden, hidden, hidden, hidden, hidden]   telephone     hidden    9850   
4  [hidden, hidden, hidden, hidden, hidden]   telephone     hidden    9851   

   promptID                                          sentence1  \
0      9847                 That which binds together Chinese.   
1      9848  The actual length of an individual worker's H-...   
2      9849                Every man I put down left me empty.   
3      9850  and uh i really think that if uh like after se...   
4      9851  yep yeah yeah it was i ended up going into ban...   

                              sentence1_binary_parse  \
0  ( ( That ( which ( binds ( together Chinese ) ...   
1  ( ( ( The ( actual length ) ) ( of ( ( an ( in...   
2  ( ( ( Every man ) ( I ( put down ) ) ) ( ( lef...   
3  ( and ( ( uh i ) ( really ( think ( ( that if ...   
4  ( ( yep yeah ) ( yeah ( ( ( ( it ( ( was i ) (...   

                                     sentence1_parse  \
0  (ROOT (FRAG (NP (NP (DT That)) (SBAR (WHNP (WD...   
1  (ROOT (S (NP (NP (DT The) (JJ actual) (NN leng...   
2  (ROOT (S (NP (NP (DT Every) (NN man)) (SBAR (S...   
3  (ROOT (FRAG (CC and) (NP (NP (FW uh) (FW i)) (...   
4  (ROOT (S (NP (NN yep) (NN yeah)) (VP (VBP yeah...   

                                           sentence2  \
0       This is a shared value among Chinese people.   
1  The location of the employer effects the lengt...   
2           I felt empty after every man I put down.   
3  Women wouldn't have gone to work after the sec...   
4           I have no idea what bankruptcy is like.    

                              sentence2_binary_parse  \
0  ( This ( ( is ( ( a ( shared value ) ) ( among...   
1  ( ( ( The location ) ( of ( the employer ) ) )...   
2  ( I ( ( ( felt ( empty ( after ( every man ) )...   
3  ( Women ( ( ( would n't ) ( have ( gone ( to (...   
4  ( I ( ( have ( ( no idea ) ( what ( bankruptcy...   

                                     sentence2_parse  
0  (ROOT (S (NP (DT This)) (VP (VBZ is) (NP (NP (...  
1  (ROOT (S (NP (NP (DT The) (NN location)) (PP (...  
2  (ROOT (S (NP (PRP I)) (VP (VBD felt) (ADJP (JJ...  
3  (ROOT (S (NP (NNP Women)) (VP (MD would) (RB n...  
4  (ROOT (S (NP (PRP I)) (VP (VBP have) (NP (NP (...

In [103]:
print(test_df.shape[0])

9796


In [104]:
sentences1 = list(test_df['sentence1'])
sentences2 = list(test_df['sentence2'])
test_pair_ids = list(test_df['pairID'])

In [105]:
test_s1 = test_df['sentence1']
test_s2 = test_df['sentence2']
print(test_s1[0])
print(test_s2[0])

That which binds together Chinese.
This is a shared value among Chinese people.


In [106]:
%%time

# initialize counters
count_c = 0
count_e = 0
count_n = 0

# This uses the pretrained Roberta MLNI model to make predictions about what class the two sentences are and assigns the output to a list
test_preds = []
with torch.no_grad():
    for k in range(len(test_s1)):
        # Encode a pair of sentences and make a prediction
        print("Pair " + str(k) + ":")
        print(test_s1[k], test_s2[k])
        tokens = roberta.encode(test_s1[k], test_s2[k])
        prediction = roberta.predict('mnli', tokens).argmax().item()
        
        # make sublist from pairIDs and semantic prediction
        test_pred = []
        test_pred.append(test_pair_ids[k])
        
        # 0 is a contradiction, 1 is neutral, and 2 is an entailment
        if prediction == 0:
            test_pred.append("contradiction")
            count_c += 1
        elif prediction == 2:
            test_pred.append("entailment")
            count_e += 1
        else:
            test_pred.append("neutral")
            count_n += 1
        test_preds.append(test_pred)
        print(prediction)
        print("-----------------")

print("done!")

Pair 0:
The new rights are nice enough Everyone really likes the newest benefits 
2
-----------------
Pair 1:
This site includes a list of all award winners and a searchable database of Government Executive articles. The Government Executive articles housed on the website are not able to be searched.
2
-----------------
Pair 2:
uh i don't know i i have mixed emotions about him uh sometimes i like him but at the same times i love to see somebody beat him I like him for the most part, but would still enjoy seeing someone beat him.
2
-----------------
Pair 3:
yeah i i think my favorite restaurant is always been the one closest  you know the closest as long as it's it meets the minimum criteria you know of good food My favorite restaurants are always at least a hundred miles away from my house. 
1
-----------------
Pair 4:
i don't know um do you do a lot of camping I know exactly.
0
-----------------
Pair 5:
well that would be a help i wish they would do that here we have got so little lan

2
-----------------
Pair 38:
Table 2: Examples of BLM's, FHWA's, IRS's, and VBA's Customer Satisfaction Expectations for Senior Executive Performance Senior Executive's have been studies on various aspects to reach the expectations.
0
-----------------
Pair 39:
In Hong Kong you can have a plate, or even a whole dinner service, hand-painted to your own design. It's impossible to have a plate hand-painted to your own design in Hong Kong.
1
-----------------
Pair 40:
There are a number of expensive jewelry and other duty-free shops, all with goods priced in US dollars (duty-free goods must always be paid for in foreign currency). Jewelry and duty-free shops are an interesting place to buy goods.
2
-----------------
Pair 41:
What's truly striking, though, is that Jobs has never really let this idea go. Jobs never held onto an idea for long.
1
-----------------
Pair 42:
While it's probably true that democracies are unlikely to go to war unless they're attacked, sometimes they are the first 

0
-----------------
Pair 80:
Justice Kennedy does not care what law librarians across the country do with all the Supreme Court Reporters from 1790 through 1998. Justice Kennedy doesn't care if the Supreme Court Reporters from 1790 to 1998 are thrown away.
2
-----------------
Pair 81:
The entire city was surrounded by open countryside with a scattering of small villages. The whole countryside is scattered with small villages. 
2
-----------------
Pair 82:
substitute my my yeah my kid'll do uh four or five hours this week for me no problem I just can't make the time because of my job.
1
-----------------
Pair 83:
it's actually there well Iraq has had uh designs on that place since nineteen twenty two so you know it wasn't like something that just suddenly popped up The weird thing is that Iraq was never interested in that place until now.
0
-----------------
Pair 84:
The final rule contains a Federalism Assessment under Executive Order The final rule had a federalism assessment that was

2
-----------------
Pair 122:
Slate 's Joseph Nocera. Nocera works for Slate.
1
-----------------
Pair 123:
This town, which flourished between 6500 and 5500 b.c. , had flat-roofed houses of mud and timber decorated with wall-paintings, some of which show patterns that still appear on Anatolian kilims. This town is over 8000 years old.
2
-----------------
Pair 124:
Candidates must submit a set of fingerprints for review by the FBI. People that want the job have to have their fingerprints sent to the FBI.
0
-----------------
Pair 125:
In 1998, Cesar Chavez fasted for 36 days in California to underscore the dangers of pesticides to farm workers and their children. Cesar Chavez was not concerned about the dangers of pesticide use.
1
-----------------
Pair 126:
The red moon made her skin glow. Her skin was glowing from the red moon.
1
-----------------
Pair 127:
Strategic parents might spend a large portion of their tax cuts, causing interest rates to rise. Tax cuts geared to parents will 

0
-----------------
Pair 165:
The only drawback is, of course, the large crowds in summer. It is pretty much deserted in July.
2
-----------------
Pair 166:
The word itself, tapa, is translated as  lid  and derives from the old custom of offering a bite of food along with a drink, the food being served on a saucer sitting on top of the glass like a lid. Tapas are only small in order for you to try a lot.
0
-----------------
Pair 167:
yeah yeah and i took a five year note out on my car when i right when i got out of college and uh i'll never do that again i still got a couple of years on it to go and i'm My biggest mistake was taking a five year note out on my car.
0
-----------------
Pair 168:
To places where surface transportation is not available, senders would be required to pay air rates, and possibly air rates keyed to the characteristics of the Alaskan air system. The Alaskan air system is an effective method of shipping.
2
-----------------
Pair 169:
were sort of a double sign w

...

2
-----------------
Pair 9589:
Nonetheless, the rationality of service tiers remains. It makes sense to keep the service tiers because they are easily understood by the client.
0
-----------------
Pair 9590:
… I saw that I must lead two lives. There was no shortage of complexity to the issue at hand, but it wasn't one that couldn't be solved by one well-thought out track. 
0
-----------------
Pair 9591:
This number represents the most reliable, albeit conservative, estimate of cases closed in 1999 by LSC grantees. This is an estimate of closed cases.
2
-----------------
Pair 9592:
yes they would they just wouldn't be able to own the kind of automobiles that they think they deserve to own or the kind of homes that we think we deserve to own we might have to you know just be able to i think if we a generation went without debt then the next generation like if if our our generation my husband and i we're twenty eight if we lived our lives and didn't become you know indebted like you know 

0
-----------------
Pair 9628:
Turns out that Bill got one letter last year that just tore at his heartstrings. Bill got one letter last year that tore at his heartstrings.
0
-----------------
Pair 9629:
Sixty percent of Americans are frustrated and angry with the health-care system, and 70 percent favor federal intervention. The majority of Americans are satisfied with the health-care system.
0
-----------------
Pair 9630:
The most recent attraction at the pyramid complex is a small museum housing the remains of a solar barque (a cedar longboat) which was found in 1954. The longboat most likely belonged to the royal family.
0
-----------------
Pair 9631:
At the delta of the Rh??ne, where its two arms spill into the Medi?­ter?­ra?­nean, the Camargue has been reclaimed from the sea to form a national nature reserve. The reclamation effort was contracted out to a Dutch company that specializes in dikes and sea water management.
2
-----------------
Pair 9632:
 Medicare gross outlay projec

2
-----------------
Pair 9672:
you know Arnold Schwarzenegger is getting to be uh a bit of a variety actor you know at first he was just a big muscle man but he's kind of branching out Arnold Schwarzenegger has never been an actor or a muscle man.
1
-----------------
Pair 9673:
Beyond the facade there are cavernous empty rooms. The rooms past the facade are cluttered with furniture.
1
-----------------
Pair 9674:
you know getting clothes and stuff every once in awhile exactly They don't ever get new clothes or stuff.
2
-----------------
Pair 9675:
Based on field observations and some discussions with U.S. It was based on field observations and discussions with the us. 
0
-----------------
Pair 9676:
Too bad it chose to use McIntyre instead. McIntyre was not picked to be used.
2
-----------------
Pair 9677:
so i'll probably say you know it's like well we've been talking for five six minutes so okay We've been talking for about 2 hours.
1
-----------------
Pair 9678:
After the second cou

1
-----------------
Pair 9713:
yeah yeah uh-huh yeah we we saw that one uh we find that uh that uh if you can get into those dollar movies you know they're uh they're a dollar and a half what is it dollar and a quarter dollar and a half now You can get it at the dollar movies.
1
-----------------
Pair 9714:
Since there is no airport on the island, all visitors must arrive at the port, Skala, where most of the hotels are located and all commercial activity is carried out. The best way to get onto the island is by plane.
0
-----------------
Pair 9715:
The house fell into ruin after emancipation, when fear of the witch's influence drove the plantation's slaves away. The slaves didn't believe in witches, and stayed on the plantation.
2
-----------------
Pair 9716:
The door did not budge. The door didn't move. 
2
-----------------
Pair 9717:
It has long been influenced by their differing traits, and has assimilated their various customs and practices. Their unique traits has created lots of

1
-----------------
Pair 9752:
36 million could mean the state's legal services for the poor will lose six of their 21 regional offices, the head of a poverty-law resource center said. The state's legal services department could lose a lot of funding.
2
-----------------
Pair 9753:
The living is not equal to the Ritz, he observed with a sigh. The living is way better than the Ritz, he pointed out cheerfully.
2
-----------------
Pair 9754:
Closed on the Sabbath. Sabbath is closed.
1
-----------------
Pair 9755:
During the half-century of its existence, Israel has absorbed approximately 2.5 million Jewish immigrants, displaced persons, refugees, and survivors of the Nazi Holocaust. Israel took in 2.5 million Jewish people as a result of the Holocaust.
2
-----------------
Pair 9756:
If you have the energy to climb the 387 steps to the top of the south tower, you will be rewarded with a stunning view over the city. There is a great view at the top of the steps.
0
-----------------
Pair 975

In [107]:
# print prediction counts as a sanity check
print("Contradictions: " + str(count_c))
print("Entailments: " + str(count_e))
print("Neutrals: " + str(count_n))

Contradictions: 3255
Entailments: 3490
Neutrals: 3051


In [110]:
# turn nested lists into a dataframe
submission_df = pd.DataFrame(test_preds, columns = ['pairID', 'gold_label'])
submission_df.head

<bound method NDFrame.head of       pairID     gold_label
0       9847     entailment
1       9848     entailment
2       9849     entailment
3       9850        neutral
4       9851  contradiction
...      ...            ...
9791   19638     entailment
9792   19639        neutral
9793   19640  contradiction
9794   19641        neutral
9795   19642  contradiction

[9796 rows x 2 columns]>

In [111]:
# export probabilities for words in each class to .csv file
submission_df.to_csv("submission.csv", index=False)

In [ ]:
########################################## END MAIN ##########################################

In [58]:
# Update April 22, 2020: Hugging Face updated run_language_modeling.py script.
# Please use this version before the update.
!wget -c https://raw.githubusercontent.com/chriskhanhtran/spanish-bert/master/run_language_modeling.py

--2022-03-21 11:24:52--  https://raw.githubusercontent.com/chriskhanhtran/spanish-bert/master/run_language_modeling.py
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 2606:50c0:8003::154, 2606:50c0:8000::154, 2606:50c0:8001::154, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|2606:50c0:8003::154|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 34328 (34K) [text/plain]
Saving to: ‘run_language_modeling.py’

run_language_modeli 100%[===================>]  33.52K  --.-KB/s    in 0.004s  

2022-03-21 11:24:52 (8.74 MB/s) - ‘run_language_modeling.py’ saved [34328/34328]



In [5]:
# must run this after the previous cell executes
from fairseq.data.data_utils import collate_tokens

In [6]:
import os
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import spacy
nlp = spacy.load("en_core_web_sm")
print(os.listdir("./input"))

['multinli_0.9_test_matched_sample_submission.csv', 'multinli_0.9_test_matched_unlabeled.jsonl', 'multinli_0.9_test_matched_unlabeled.jsonl.zip', 'multinli_0.9_test_matched_unlabeled.txt', 'multinli_0.9_test_matched_unlabeled.txt.zip']


In [7]:
df = pd.read_json("./input/multinli_0.9_test_matched_unlabeled.jsonl", lines=True)
df.head(5)

annotator_labels       genre gold_label  pairID  \
0  [hidden, hidden, hidden, hidden, hidden]       slate     hidden    9847   
1  [hidden, hidden, hidden, hidden, hidden]  government     hidden    9848   
2  [hidden, hidden, hidden, hidden, hidden]     fiction     hidden    9849   
3  [hidden, hidden, hidden, hidden, hidden]   telephone     hidden    9850   
4  [hidden, hidden, hidden, hidden, hidden]   telephone     hidden    9851   

   promptID                                          sentence1  \
0      9847                 That which binds together Chinese.   
1      9848  The actual length of an individual worker's H-...   
2      9849                Every man I put down left me empty.   
3      9850  and uh i really think that if uh like after se...   
4      9851  yep yeah yeah it was i ended up going into ban...   

                              sentence1_binary_parse  \
0  ( ( That ( which ( binds ( together Chinese ) ...   
1  ( ( ( The ( actual length ) ) ( of ( ( an ( in...   
2  ( ( ( Every man ) ( I ( put down ) ) ) ( ( lef...   
3  ( and ( ( uh i ) ( really ( think ( ( that if ...   
4  ( ( yep yeah ) ( yeah ( ( ( ( it ( ( was i ) (...   

                                     sentence1_parse  \
0  (ROOT (FRAG (NP (NP (DT That)) (SBAR (WHNP (WD...   
1  (ROOT (S (NP (NP (DT The) (JJ actual) (NN leng...   
2  (ROOT (S (NP (NP (DT Every) (NN man)) (SBAR (S...   
3  (ROOT (FRAG (CC and) (NP (NP (FW uh) (FW i)) (...   
4  (ROOT (S (NP (NN yep) (NN yeah)) (VP (VBP yeah...   

                                           sentence2  \
0       This is a shared value among Chinese people.   
1  The location of the employer effects the lengt...   
2           I felt empty after every man I put down.   
3  Women wouldn't have gone to work after the sec...   
4           I have no idea what bankruptcy is like.    

                              sentence2_binary_parse  \
0  ( This ( ( is ( ( a ( shared value ) ) ( among...   
1  ( ( ( The location ) ( of ( the employer ) ) )...   
2  ( I ( ( ( felt ( empty ( after ( every man ) )...   
3  ( Women ( ( ( would n't ) ( have ( gone ( to (...   
4  ( I ( ( have ( ( no idea ) ( what ( bankruptcy...   

                                     sentence2_parse  
0  (ROOT (S (NP (DT This)) (VP (VBZ is) (NP (NP (...  
1  (ROOT (S (NP (NP (DT The) (NN location)) (PP (...  
2  (ROOT (S (NP (PRP I)) (VP (VBD felt) (ADJP (JJ...  
3  (ROOT (S (NP (NNP Women)) (VP (MD would) (RB n...  
4  (ROOT (S (NP (PRP I)) (VP (VBP have) (NP (NP (...

In [8]:
# output number of rows in dataframe
print(df.shape[0])

9796


In [9]:
sentences1 = list(df['sentence1'])
sentences2 = list(df['sentence2'])
pair_ids = list(df['pairID'])

In [10]:
# create list of tuples for each sentence to 
all_pair_items = []

for i in range(len(sentences1)):
    pair_item = []
    pair_item.append(pair_ids[i])
    pair_item.append(sentences1[i])
    pair_item.append(sentences2[i])
    all_pair_items.append(pair_item)

In [11]:
all_pair_items

[[9847,
  'That which binds together Chinese.',
  'This is a shared value among Chinese people.'],
 [9848,
  "The actual length of an individual worker's H-2A visa varies depending upon the geographic location of the employer and the nature of the farmwork to be performed.",
  "The location of the employer effects the length of the worker's H-2A visa."],
 [9849,
  'Every man I put down left me empty.',
  'I felt empty after every man I put down.'],
 [9850,
  "and uh i really think that if uh like after second World War when women went to work in factories and all that that was like out of necessity because the men weren't here anymore",
  "Women wouldn't have gone to work after the second world war if men were still around."],
 [9851,
  "yep yeah yeah it was i ended up going into bankruptcy you know it was one of those things  uh oh it'll get better next week you know  things will pick up and so there i was in old bankruptcy court",
  'I have no idea what bankruptcy is like. '],
 [9852

In [ ]:
# truncate set for now because kernel is crashing
# pair_items = all_pair_items[0:101]
# pair_items = all_pair_items[101:201]
pair_items = all_pair_items[201:301]
print(len(pair_items))
print(len(all_pair_items))

In [38]:
pair_items = [
    ['Roberta is a heavily optimized version of BERT.', 'Roberta is not very optimized.'],
    ['Roberta is a heavily optimized version of BERT.', 'Roberta is based on BERT.'],
    ['potatoes are awesome.', 'I like to run.'],
    ['Mars is very far from earth.', 'Mars is very close.'],
]

In [39]:
pair_batch = collate_tokens(
    [roberta.encode(pair_item[1], pair_item[2]) for pair in pair_items], pad_idx=1
)

In [40]:
logprobs = roberta.predict('mnli', pair_batch)
print(logprobs.argmax(dim=1))

tensor([0, 0, 0, 0])


In [41]:
# create nested lists of pairIDs and the prediction turned into the semantic representation
preds = []
count_c = 0
count_e = 0
count_n = 0

probs = logprobs.argmax(dim=1).tolist()

for j in range(len(probs)):
    # print(probs[j])
    pred = []
    pred.append(pair_items[j][0])
    if probs[j] == 0:
        pred.append("contradiction")
        count_c += 1
    elif probs[j] == 2:
        pred.append("entailment")
        count_e += 1
    else:
        pred.append("neutral")
        count_n += 1
    preds.append(pred)

In [35]:
# print prediction counts as a sanity check
print("Contradictions: " + str(count_c))
print("Entailments: " + str(count_e))
print("Neutrals: " + str(count_n))

Contradictions: 49
Entailments: 0
Neutrals: 0


In [ ]:
# turn nested lists into a dataframe
submission_df = pd.DataFrame(preds, columns = ['pairID', 'gold_label'])

In [ ]:
# export probabilities for words in each class to .csv file
submission_df.to_csv("submission.csv", index=False)

In [60]:
from transformers import pipeline

fill_mask = pipeline(
    "fill-mask",
    model="roberta-base",
    tokenizer="roberta-base"
)
fill_mask("Send these <mask> back!")

Downloading:   0%|          | 0.00/481 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/478M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/878k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/446k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.29M [00:00<?, ?B/s]

[{'score': 0.16661450266838074,
  'token': 3493,
  'token_str': ' pictures',
  'sequence': 'Send these pictures back!'},
 {'score': 0.10792748630046844,
  'token': 2356,
  'token_str': ' photos',
  'sequence': 'Send these photos back!'},
 {'score': 0.07670953869819641,
  'token': 5575,
  'token_str': ' emails',
  'sequence': 'Send these emails back!'},
 {'score': 0.048607684671878815,
  'token': 3156,
  'token_str': ' images',
  'sequence': 'Send these images back!'},
 {'score': 0.04841744154691696,
  'token': 5430,
  'token_str': ' letters',
  'sequence': 'Send these letters back!'}]

In [61]:
!git clone https://github.com/cardiffnlp/tweeteval /tmp/tweeteval

from transformers import RobertaTokenizer, RobertaForMaskedLM

tokenizer = RobertaTokenizer.from_pretrained('roberta-base')
model = RobertaForMaskedLM.from_pretrained('roberta-base')

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
Cloning into '/tmp/tweeteval'...
remote: Enumerating objects: 367, done.
remote: Counting objects: 100% (49/49), done.
remote: Compressing objects: 100% (45/45), done.
remote: Total 367 (delta 21), reused 13 (delta 4), pack-reused 318
Receiving objects: 100% (367/367), 10.79 MiB | 2.33 MiB/s, done.
Resolving deltas: 100% (112/112), done.


In [66]:
from transformers import LineByLineTextDataset

dataset = LineByLineTextDataset(
    tokenizer=tokenizer,
    # file_path="/tmp/tweeteval/datasets/hate/train_text.txt",
    file_path="./multinli_1.0/multinli_1.0_dev_matched.txt",
    block_size=512,
)

Creating features from dataset file at ./multinli_1.0/multinli_1.0_dev_matched.txt


In [67]:
from transformers import DataCollatorForLanguageModeling

data_collator = DataCollatorForLanguageModeling(
    tokenizer=tokenizer, mlm=True, mlm_probability=0.15
)

In [68]:
from transformers import Trainer, TrainingArguments

training_args = TrainingArguments(
    output_dir="./roberta-retrained",
    overwrite_output_dir=True,
    num_train_epochs=25,
    per_device_train_batch_size=48,
    save_steps=500,
    save_total_limit=2,
    seed=1
)

trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=dataset
)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).


In [ ]:
trainer.train()

trainer.save_model("./roberta-retrained")

***** Running training *****
  Num examples = 10001
  Num Epochs = 25
  Instantaneous batch size per device = 48
  Total train batch size (w. parallel, distributed & accumulation) = 48
  Gradient Accumulation steps = 1
  Total optimization steps = 5225


In [ ]:
%reload_ext tensorboard

%tensorboard --logdir ./runs

In [ ]:
from transformers import pipeline

fill_mask = pipeline(
    "fill-mask",
    model="./roberta-retrained",
    tokenizer="roberta-base"
)
fill_mask("Send these <mask> back!")